### $\textbf{NOTE: Please run the code in Jupyter Notebook as I have included animation(s)}\\  \textbf{which may not run on Google Colab}$

## $\textit{Importing Necessary Libraries}$

In [1]:
import numpy as np
import matplotlib.pyplot as plt

%matplotlib qt

# $\underline{\text{Problem 1 - Flux Limiters}}$

## $\textit{Flip-Flop Function}$

In [2]:
def flip_flop(vel_int):
    return 1 if vel_int >= 0 else -1

## $\textit{Flux Limiter Functions}$

In [3]:
def flux_int(vel_int,ql_2,ql_1,q_0,dt,dx,limiter):
    
    theta = flip_flop(vel_int)
    r = (ql_1 - ql_2)/(q_0 - ql_1)
    
    if limiter == "Donor Cell":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*0.0*(q_0-ql_1)

        flux_val = term1 + term2

        return flux_val
    
    elif limiter == "Lax Wendroff":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*1.0*(q_0-ql_1)

        flux_val = term1 + term2

        return flux_val
    
    elif limiter == "Beam Warming":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        if q_0 == ql_1: 
            term2 = 0
        else:
            term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*r*(q_0-ql_1)

        flux_val = term1 + term2

        return flux_val
    
    elif limiter == "Fromm":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        if q_0 == ql_1:
            term2 = 0
        else:
            term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*0.5*(1+r)*(q_0-ql_1)

        flux_val = term1 + term2

        return flux_val
    
    elif limiter == "minmod":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        if q_0 == ql_1:
            term2 = 0
        else:
            minmod = max(0, min(1,r))
            term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*minmod*(q_0 - ql_1)
        
        flux_val = term1 + term2
        
        return flux_val
    
    elif limiter == "superbee":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        if q_0 == ql_1:
            term2 = 0
        else:
            superbee = max(0, min(1, 2*r), min(2, r))        
            term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*superbee*(q_0 - ql_1)
        
        flux_val = term1 + term2
        
        return flux_val
    
    elif limiter == "mc":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        if q_0 == ql_1:
            term2 = 0
        else:
            mc = max(0, min(0.5*(1+r), 2, 2*(r)))
            term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*mc*(q_0-ql_1)
        
        flux_val = term1 + term2
        
        return flux_val
        
    elif limiter == "vanleer":
        
        term1 = 0.5*vel_int*(ql_1*(1+theta) + q_0*(1-theta))
        if q_0 == ql_1:
            term2 = 0
        else:
            vanleer1 = r + abs(r)
            vanleer2 = 1 + abs(r)
            vanleer = vanleer1/vanleer2
            
            term2 = 0.5*abs(vel_int)*(1-abs(vel_int*dt/dx))*vanleer*(q_0 - ql_1)
        
        flux_val = term1 + term2
        
        return flux_val

## $\textit{Pulse Function}$

In [26]:
def pulse(t,x,problem):
    sigma = 1.0
    q = np.zeros([len(t),len(x)])
    
    if problem == "Square Pulse": 
        
        for i in range(len(x)):
            q[0][i] = 0.00001 if x[i] < -2 or x[i] > 2 else 1
        
        return q

    elif problem == "Gaussian Pulse":    
        
        q[0,:] = (1/(sigma*np.sqrt(2*np.pi)))*np.exp(-(x**2)/(2*(sigma**2)))
        
        return q

## $\textit{Initial Condition}$

In [23]:
x_vals = np.linspace(-10,10,200,endpoint=True)
t_vals = np.linspace(0,10,1000,endpoint=True)

adv_vel = 3.0
sigma = 1.0
pi = np.pi

dt = t_vals[1] - t_vals[0]
dx = x_vals[1] - x_vals[0]

print(dt/dx)

0.0995995995995996


## $\underline{\textbf{Gaussian Wave}}$

In [243]:
problem = "Gaussian Pulse"
q_vals = pulse(t_vals,x_vals,problem)

### $\text{Donor Cell}$

In [244]:
limiter = "Donor Cell"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_donor = q_vals 

KeyboardInterrupt: 

### $\text{Lax Wendroff}$

In [ ]:
limiter = "Lax Wendroff"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_laxwend = q_vals

### $\text{Beam-Warming}$

In [247]:
limiter = "Beam Warming"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.37,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_beamwarm = q_vals

KeyboardInterrupt: 

### $\text{Fromm}$

In [248]:
limiter = "Fromm"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.37,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_fromm = q_vals

KeyboardInterrupt: 

### $\text{Min-Mod}$

In [157]:
limiter = "minmod"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_minmod = q_vals

### $\text{Superbee}$

In [184]:
limiter = "superbee"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_superbee = q_vals

0
2.644192166706179e-22
2.644192166706179e-22
7.073204570401705e-22
7.073204570401705e-22
1.8728845932155575e-21
1.8728845932155575e-21
4.9088128520033e-21
4.9088128520033e-21
1.273537182644495e-20
1.273537182644495e-20
3.2705100343718415e-20
3.2705100343718415e-20
8.313559680697867e-20
8.313559680697867e-20
2.0918241296623755e-19
2.0918241296623755e-19
5.209893435745528e-19
5.209893435745528e-19
1.2843899645342223e-18
1.2843899645342223e-18
3.1342107044783666e-18
3.1342107044783666e-18
7.570446410272806e-18
7.570446410272806e-18
1.809987406956313e-17
1.809987406956313e-17
4.2834044851597055e-17
4.2834044851597055e-17
1.0033691681661451e-16
1.0033691681661451e-16
2.3264255579942385e-16
2.3264255579942385e-16
5.339159265526695e-16
5.339159265526695e-16
1.2128592624818397e-15
1.2128592624818397e-15
2.7270946786870947e-15
2.7270946786870947e-15
6.06932919900362e-15
6.06932919900362e-15
1.3369962258301358e-14
1.3369962258301358e-14
2.915190574666373e-14
2.915190574666373e-14
6.291427704884

4.852780620814449e-22
0
0
0
0
2.6530529994200734e-22
2.6530529994200734e-22
7.088062779845329e-22
7.088062779845329e-22
1.876795293155797e-21
1.876795293155797e-21
4.9189985087695486e-21
4.9189985087695486e-21
1.2761628988345612e-20
1.2761628988345612e-20
3.277209322229365e-20
3.277209322229365e-20
8.330476918307357e-20
8.330476918307357e-20
2.0960522562349067e-19
2.0960522562349067e-19
5.220352237286059e-19
5.220352237286059e-19
1.2869504887514593e-18
1.2869504887514593e-18
3.140414913260543e-18
3.140414913260543e-18
7.58532466231761e-18
7.58532466231761e-18
1.813518610554952e-17
1.813518610554952e-17
4.29169909946862e-17
4.29169909946862e-17
1.0052974449704685e-16
1.0052974449704685e-16
2.330862046336293e-16
2.330862046336293e-16
5.349261164772231e-16
5.349261164772231e-16
1.215135707979937e-15
1.215135707979937e-15
2.732171579872044e-15
2.732171579872044e-15
6.080534511064592e-15
6.080534511064592e-15
1.3394437636929762e-14
1.3394437636929762e-14
2.9204812532875235e-14
2.92048125328

3.37932549546734e-21
0
0
0
0
0
0
0
0
2.661943475721624e-22
2.661943475721624e-22
7.102941141671345e-22
7.102941141671345e-22
1.880714129714643e-21
1.880714129714643e-21
4.929205217625397e-21
4.929205217625397e-21
1.278794006657523e-20
1.278794006657523e-20
3.2839222753680565e-20
3.2839222753680565e-20
8.34742843163686e-20
8.34742843163686e-20
2.1002888906770727e-19
2.1002888906770727e-19
5.230831937447828e-19
5.230831937447828e-19
1.2895160930799385e-18
1.2895160930799385e-18
3.1466313423931942e-18
3.1466313423931942e-18
7.600232004440022e-18
7.600232004440022e-18
1.817056666710518e-17
1.817056666710518e-17
4.3000096873697224e-17
4.3000096873697224e-17
1.0072294063730849e-16
1.0072294063730849e-16
2.335306944960799e-16
2.335306944960799e-16
5.359382059878502e-16
5.359382059878502e-16
1.2174163989914362e-15
1.2174163989914362e-15
2.7372578700490536e-15
2.7372578700490536e-15
6.091760368766665e-15
6.091760368766665e-15
1.3418957501891639e-14
1.3418957501891639e-14
2.925781462803832e-14
2

2.259735739581292e-20
0
0
0
0
0
0
0
0
0
0
0
0
2.670863694616779e-22
2.670863694616779e-22
7.117839624423634e-22
7.117839624423634e-22
1.8846411234227017e-21
1.8846411234227017e-21
4.939433021897092e-21
4.939433021897092e-21
1.2814305171382652e-20
1.2814305171382652e-20
3.290648921541994e-20
3.290648921541994e-20
8.364414289821136e-20
8.364414289821136e-20
2.1045340500292045e-19
2.1045340500292045e-19
5.2413325777899505e-19
5.2413325777899505e-19
1.2920867875486206e-18
1.2920867875486206e-18
3.1528600158227947e-18
3.1528600158227947e-18
7.615168493214065e-18
7.615168493214065e-18
1.820601588647432e-17
1.820601588647432e-17
4.308336279448417e-17
4.308336279448417e-17
1.009165059372781e-16
1.009165059372781e-16
2.3397602697129037e-16
2.3397602697129037e-16
5.3695219863372395e-16
5.3695219863372395e-16
1.2197013433815081e-15
1.2197013433815081e-15
2.7423535664618735e-15
2.7423535664618735e-15
6.103006809511434e-15
6.103006809511434e-15
1.3443521933442426e-14
1.3443521933442426e-14
2.931091

1.4508316729054242e-19
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
2.67981375544161e-22
2.67981375544161e-22
7.132758196211144e-22
7.132758196211144e-22
1.8885762948898695e-21
1.8885762948898695e-21
4.949681964987375e-21
4.949681964987375e-21
1.2840724413241186e-20
1.2840724413241186e-20
3.297389288561371e-20
3.297389288561371e-20
8.381434562133753e-20
8.381434562133753e-20
2.1087877513656e-19
2.1087877513656e-19
5.251854199953781e-19
5.251854199953781e-19
1.2946625822061672e-18
1.2946625822061672e-18
3.1591009575424845e-18
3.1591009575424845e-18
7.630134185323186e-18
7.630134185323186e-18
1.8241533896154916e-17
1.8241533896154916e-17
4.316678906348311e-17
4.316678906348311e-17
1.0111044109815595e-16
1.0111044109815595e-16
2.3442220364674074e-16
2.3442220364674074e-16
5.379680979706038e-16
5.379680979706038e-16
1.2219905490297923e-15
1.2219905490297923e-15
2.7474586863857025e-15
2.7474586863857025e-15
6.114273870768046e-15
6.114273870768046e-15
1.3468131011981206e-14
1.3468131011981206e-14
2.93641

...

0.04817175640452423
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
4.279871546544212e-22
4.279871546544212e-22
9.396132077805675e-22
9.396132077805675e-22
2.5314023807094652e-21
2.5314023807094652e-21
6.6147305143132236e-21
6.6147305143132236e-21
1.7129435212246744e-20
1.7129435212246744e-20
4.390467632127398e-20
4.390467632127398e-20
1.1138800911155711e-19
1.1138800911155711e-19
2.7972030563855693e-19
2.7972030563855693e-19
6.952904538912972e-19
6.952904538912972e-19
1.7106612734604698e-18
1.7106612734604698e-18
4.165968584668082e-18
4.165968584668082e-18
1.0042014659804844e-17
1.0042014659804844e-17
2.3959472123651686e-17
2.3959472123651686e-17
5.658271324518251e-17
5.6582

0.04610592436926686
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
4.294202132010323e-22
4.294202132010323e-22
9.41330616027382e-22
9.41330616027382e-22
2.536743058719931e-21
2.536743058719931e-21
6.6284301036160926e-21
6.6284301036160926e-21
1.7164710466948706e-20
1.7164710466948706e-20
4.3994498993700405e-20
4.3994498993700405e-20
1.1161438430148112e-19
1.1161438430148112e-19
2.8028495603811846e-19
2.8028495603811846e-19
6.966843698346539e-19
6.966843698346539e-19
1.7140669008775792e-18
1.7140669008775792e-18
4.17420349140951e-18
4.17420349140951e-18
1.0061721570628156e-17
1.0061721570628156e-17
2.400614600820146e-17
2.400614600820146e-17
5.669211442120476e-17
5.66

0.039743964200739335
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
4.308580621511063e-22
4.308580621511063e-22
9.430489907800899e-22
9.430489907800899e-22
2.5420958905249062e-21
2.5420958905249062e-21
6.642157736384503e-21
6.642157736384503e-21
1.7200058102614597e-20
1.7200058102614597e-20
4.40845046502594e-20
4.40845046502594e-20
1.1184121754741745e-19
1.1184121754741745e-19
2.808507411057008e-19
2.808507411057008e-19
6.980810672339997e-19
6.980810672339997e-19
1.7174792755066285e-18
1.7174792755066285e-18
4.1824545946529284e-18
4.1824545946529284e-18
1.0081466954676566e-17
1.0081466954676566e-17
2.4052910326818045e-17
2.4052910326818045e-17
5.6801725944595

0.029249649656506338
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
4.323007174911754e-22
4.323007174911754e-22
9.447683193098183e-22
9.447683193098183e-22
2.547460913608256e-21
2.547460913608256e-21
6.655913465933634e-21
6.655913465933634e-21
1.7235478267980902e-20
1.7235478267980902e-20
4.417469366196727e-20
4.417469366196727e-20
1.1206850977204697e-19
1.1206850977204697e-19
2.8141766311077337e-19
2.8141766311077337e-19
6.994805516126833e-19
6.994805516126833e-19
1.7208984106481999e-18
1.7208984106481999e-18
4.1907219260884544e-18
4.1907219260884544e-18
1.0101250886656192e-17
1.0101250886656192e-17
2.4099765253746933e-17
2.4099765253746933e-17
5.691

0.015489905220110955
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
4.337481952610317e-22
4.337481952610317e-22
9.464885887919798e-22
9.464885887919798e-22
2.5528381656217967e-21
2.5528381656217967e-21
6.669697345631992e-21
6.669697345631992e-21
1.727097111210412e-20
1.727097111210412e-20
4.426506640058597e-20
4.426506640058597e-20
1.122962618999008e-19
1.122962618999008e-19
2.8198572432732476e-19
2.8198572432732476e-19
7.008828285049637e-19
7.008828285049637e-19
1.7243243196289561e-18
1.7243243196289561e-18
4.199005517467877e-18
4.199005517467877e-18
1.012107344141743e-17
1.012107344141743e-17
2.41467109635674e-17
2.41467109635674e-17
5.70215

### $\text{MC}$

In [183]:
limiter = "mc"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_mc = q_vals

0
2.4293491842769712e-22
2.4293491842769712e-22
6.45051262563932e-22
6.45051262563932e-22
1.6954243613047143e-21
1.6954243613047143e-21
4.4110461696120626e-21
4.4110461696120626e-21
1.1360118042540841e-20
1.1360118042540841e-20
2.896017428767427e-20
2.896017428767427e-20
7.307950244330405e-20
7.307950244330405e-20
1.825429391351976e-19
1.825429391351976e-19
4.513448270271938e-19
4.513448270271938e-19
1.1046501672531472e-18
1.1046501672531472e-18
2.6761642786877933e-18
2.6761642786877933e-18
6.4175801199589834e-18
6.4175801199589834e-18
1.5233479730290045e-17
1.5233479730290045e-17
3.579274041705289e-17
3.579274041705289e-17
8.32448681540096e-17
8.32448681540096e-17
1.9163962058802337e-16
1.9163962058802337e-16
4.366937972586273e-16
4.366937972586273e-16
9.849884852922337e-16
9.849884852922337e-16
2.1991059694226787e-15
2.1991059694226787e-15
4.8598228643262446e-15
4.8598228643262446e-15
1.0630467001241272e-14
1.0630467001241272e-14
2.30165456988778e-14
2.30165456988778e-14
4.9326699116

6.598512475530451e-23
0
0
0
0
2.4360616649775395e-22
2.4360616649775395e-22
6.4663403683897335e-22
6.4663403683897335e-22
1.699585486676882e-21
1.699585486676882e-21
4.4218694829789704e-21
4.4218694829789704e-21
1.138797133684968e-20
1.138797133684968e-20
2.90310935639856e-20
2.90310935639856e-20
7.325816249542685e-20
7.325816249542685e-20
1.829882565427622e-19
1.829882565427622e-19
4.524430592025874e-19
4.524430592025874e-19
1.1073299758104617e-18
1.1073299758104617e-18
2.682634229321294e-18
2.682634229321294e-18
6.43303579158602e-18
6.43303579158602e-18
1.5270011129406788e-17
1.5270011129406788e-17
3.58781757867503e-17
3.58781757867503e-17
8.344256658602699e-17
8.344256658602699e-17
1.9209227182769957e-16
1.9209227182769957e-16
4.377192595935425e-16
4.377192595935425e-16
9.872871279935079e-16
9.872871279935079e-16
2.2042041937474765e-15
2.2042041937474765e-15
4.871011104818268e-15
4.871011104818268e-15
1.0654761022550056e-14
1.0654761022550056e-14
2.3068740936713693e-14
2.30687409367

4.665118712322985e-22
0
0
0
0
0
0
0
0
2.442788721971318e-22
2.442788721971318e-22
6.482206365857701e-22
6.482206365857701e-22
1.703756836812335e-21
1.703756836812335e-21
4.432719382073282e-21
4.432719382073282e-21
1.141589298815877e-20
1.141589298815877e-20
2.9102186647100185e-20
2.9102186647100185e-20
7.343725957641653e-20
7.343725957641653e-20
1.8343466068203817e-19
1.8343466068203817e-19
4.535439638416236e-19
4.535439638416236e-19
1.1100162839592257e-18
1.1100162839592257e-18
2.6891198132971064e-18
2.6891198132971064e-18
6.448528652266266e-18
6.448528652266266e-18
1.5306630023107433e-17
1.5306630023107433e-17
3.596381474556094e-17
3.596381474556094e-17
8.364073354994959e-17
8.364073354994959e-17
1.9254598951196696e-16
1.9254598951196696e-16
4.387471227206939e-16
4.387471227206939e-16
9.895911162160829e-16
9.895911162160829e-16
2.2093141899628183e-15
2.2093141899628183e-15
4.882224985658144e-15
4.882224985658144e-15
1.0679110280017643e-14
1.0679110280017643e-14
2.3121053865923477e-14

3.1657881416411175e-21
0
0
0
0
0
0
0
0
0
0
0
0
2.449530393226409e-22
2.449530393226409e-22
6.498110715320606e-22
6.498110715320606e-22
1.70793843691965e-21
1.70793843691965e-21
4.443595932273992e-21
4.443595932273992e-21
1.1443883164396271e-20
1.1443883164396271e-20
2.9173453963320564e-20
2.9173453963320564e-20
7.361679475591796e-20
7.361679475591796e-20
1.8388215420582714e-19
1.8388215420582714e-19
4.546475474475134e-19
4.546475474475134e-19
1.1127091074581939e-18
1.1127091074581939e-18
2.6956210683636504e-18
2.6956210683636504e-18
6.464058791385568e-18
6.464058791385568e-18
1.5343336620630236e-17
1.5343336620630236e-17
3.6049657777683675e-17
3.6049657777683675e-17
8.383937015348152e-17
8.383937015348152e-17
1.9300077614605134e-16
1.9300077614605134e-16
4.3977739224150127e-16
4.3977739224150127e-16
9.919004623416824e-16
9.919004623416824e-16
2.214435985126906e-15
2.214435985126906e-15
4.893464565305165e-15
4.893464565305165e-15
1.070351489851051e-14
1.070351489851051e-14
2.31734847501

2.062524543114949e-20
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
2.4562867168117867e-22
2.4562867168117867e-22
6.514053514287928e-22
6.514053514287928e-22
1.712130312269109e-21
1.712130312269109e-21
4.454499199121047e-21
4.454499199121047e-21
1.1471942033903295e-20
1.1471942033903295e-20
2.9244895939995745e-20
2.9244895939995745e-20
7.379676910619549e-20
7.379676910619549e-20
1.8433073977340744e-19
1.8433073977340744e-19
4.557538165392907e-19
4.557538165392907e-19
1.1154084621043127e-18
1.1154084621043127e-18
2.7021380323604113e-18
2.7021380323604113e-18
6.479626298544325e-18
6.479626298544325e-18
1.5380131131712937e-17
1.5380131131712937e-17
3.613570536846636e-17
3.613570536846636e-17
8.403847750693835e-17
8.403847750693835e-17
1.9345663424104445e-16
1.9345663424104445e-16
4.4081007377040137e-16
4.4081007377040137e-16
9.94215178780583e-16
9.94215178780583e-16
2.219569606359818e-15
2.219569606359818e-15
4.904729902351129e-15
4.904729902351129e-15
1.0727975003175596e-14
1.0727975003175596e-14
2.32

...

0.012043113971080419
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3.56637691454799e-22
3.56637691454799e-22
9.17529875493612e-22
9.17529875493612e-22
2.4133332631663185e-21
2.4133332631663185e-21
6.278182177405179e-21
6.278182177405179e-21
1.616430592001696e-20
1.616430592001696e-20
4.118925479927556e-20
4.118925479927556e-20
1.0387611693803095e-19
1.0387611693803095e-19
2.592706849311481e-19
2.592706849311481e-19
6.404688448877211e-19
6.404688448877211e-19
1.5658506843806075e-18
1.5658506843806075e-18
3.788883018162638e-18
3.788883018162638e-18
9.073633564363114e-18
9.073633564363114e-18
2.1506069818843263e-17
2.1506069818843263e-17
5.044883415078893e-17
5.044883415078893

0.011788239709892484
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3.575632272522342e-22
3.575632272522342e-22
9.19776048581989e-22
9.19776048581989e-22
2.419259231091034e-21
2.419259231091034e-21
6.2935927867051056e-21
6.2935927867051056e-21
1.6203951755653898e-20
1.6203951755653898e-20
4.1290149199474917e-20
4.1290149199474917e-20
1.0413011793081756e-19
1.0413011793081756e-19
2.5990325518298954e-19
2.5990325518298954e-19
6.420272944748504e-19
6.420272944748504e-19
1.5696490132957911e-18
1.5696490132957911e-18
3.7980412771880746e-18
3.7980412771880746e-18
9.095478869273307e-18
9.095478869273307e-18
2.1557620215828396e-17
2.1557620215828396e-17
5.0569181939024315e-1

0.010470977209719345
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3.5849088222616726e-22
3.5849088222616726e-22
9.220277174308508e-22
9.220277174308508e-22
2.4251997711079243e-21
2.4251997711079243e-21
6.309041265040134e-21
6.309041265040134e-21
1.6243694923923682e-20
1.6243694923923682e-20
4.1391290938748745e-20
4.1391290938748745e-20
1.0438474037081963e-19
1.0438474037081963e-19
2.605373692854807e-19
2.605373692854807e-19
6.435895364007224e-19
6.435895364007224e-19
1.5734565534923335e-18
1.5734565534923335e-18
3.807221659692317e-18
3.807221659692317e-18
9.117376717286045e-18
9.117376717286045e-18
2.1609294012647373e-17
2.1609294012647373e-17
5.06898163145

0.0080881690940873
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3.5942066186564764e-22
3.5942066186564764e-22
9.2428489577613e-22
9.2428489577613e-22
2.4311549190958455e-21
2.4311549190958455e-21
6.3245277055752364e-21
6.3245277055752364e-21
1.628353566402627e-20
1.628353566402627e-20
4.1492680623929983e-20
4.1492680623929983e-20
1.0463998577934234e-19
1.0463998577934234e-19
2.611730310075855e-19
2.611730310075855e-19
6.4515557989326185e-19
6.4515557989326185e-19
1.5772733272997256e-18
1.5772733272997256e-18
3.816424219077808e-18
3.816424219077808e-18
9.139327234631758e-18
9.139327234631758e-18
2.1661091504217115e-17
2.1661091504217115e-17
5.0810737

0.004813596533624703
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
3.6035257167341177e-22
3.6035257167341177e-22
9.265475973869041e-22
9.265475973869041e-22
2.437124711021887e-21
2.437124711021887e-21
6.340052201704903e-21
6.340052201704903e-21
1.632347421575005e-20
1.632347421575005e-20
4.159431886334164e-20
4.159431886334164e-20
1.0489585568141692e-19
1.0489585568141692e-19
2.61810244127471e-19
2.61810244127471e-19
6.467254342028445e-19
6.467254342028445e-19
1.5810993571015616e-18
1.5810993571015616e-18
3.825649008875762e-18
3.825649008875762e-18
9.161330547843706e-18
9.161330547843706e-18
2.1713012986158058e-17
2.1713012986158058e-17
5.093

### $\text{van Leer}$

In [245]:
limiter = "vanleer"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.37,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals[n,i-2],q_vals[n,i-1],q_vals[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals[n,i-1],q_vals[n,i],q_vals[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals[n+1,i] = q_vals[n,i] - (dt/dx)*df
        
    q_vals[n+1,0] = q_vals[n,-2]
    q_vals[n+1,-1] = q_vals[n,1]
        
    res.set_ydata(q_vals[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()

q_vals_vanleer = q_vals

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

...

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Condition
2nd Co

KeyboardInterrupt: 

## $\underline{\textbf{Square Wave}}$

In [324]:
problem_square = "Square Pulse"
q_vals_square = pulse(t_vals,x_vals,problem_square)

### $\text{Donor Cell}$

In [25]:
limiter = "Donor Cell"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_square_donor = q_vals_square

/tmp/ipykernel_637136/2436966632.py:4: RuntimeWarning: invalid value encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)


KeyboardInterrupt: 

### $\text{Lax Wendroff}$

In [ ]:
limiter = "Lax Wendroff"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_square_laxwend = q_vals_square

### $\text{Beam-Warming}$

In [325]:
limiter = "Beam Warming"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.37,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_square_beamwarm = q_vals_square

/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: invalid value encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)
/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: divide by zero encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)


### $\text{Fromm}$

In [291]:
limiter = "Fromm"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.37,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_square_fromm = q_vals_square

/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: invalid value encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)
/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: divide by zero encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)


KeyboardInterrupt: 

### $\text{Min-Mod}$

In [292]:
limiter = "minmod"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_square_minmod = q_vals_square

/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: invalid value encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)
/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: divide by zero encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)


KeyboardInterrupt: 

### $\text{Superbee}$

In [293]:
limiter = "superbee"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_square_superbee = q_vals_square

/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: invalid value encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)
/tmp/ipykernel_9317/2436966632.py:4: RuntimeWarning: divide by zero encountered in double_scalars
  r = (ql_1 - ql_2)/(q_0 - ql_1)


KeyboardInterrupt: 

### $\text{MC}$

In [ ]:
limiter = "mc"
fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()
    
q_vals_square_mc = q_vals_square

### $\text{van Leer}$

In [ ]:
limiter = "vanleer"

fig, ax = plt.subplots(figsize=(14,8),dpi=80)
res, = ax.plot(x_vals,q_vals_square[0],lw=3.0,ls='-',color='r')
plt.xticks(size=15)
plt.yticks(size=15)
plt.xlabel("Increasing $x$ values $\longrightarrow$",size=18)
plt.ylabel("Increasing $q$ Values",size=18)
plt.title(limiter,size=20,fontweight='bold')
text = ax.text(8.5,0.97,r'Time: 0.00',fontsize=15,bbox={'facecolor':'pink','alpha':0.8,'pad':16})
plt.pause(2)

for n in range(len(t_vals)-1):
    for i in range(1,len(x_vals)-1):
        
        flux_left = flux_int(adv_vel,q_vals_square[n,i-2],q_vals_square[n,i-1],q_vals_square[n,i],dt,dx,limiter)
        flux_right = flux_int(adv_vel,q_vals_square[n,i-1],q_vals_square[n,i],q_vals_square[n,i+1],dt,dx,limiter)
        
        df = flux_right - flux_left
        
        q_vals_square[n+1,i] = q_vals_square[n,i] - (dt/dx)*df
        
    q_vals_square[n+1,0] = q_vals_square[n,-2]
    q_vals_square[n+1,-1] = q_vals_square[n,1]
        
    res.set_ydata(q_vals_square[n+1])
    text.set_text(r'Time: %.2f'%t_vals[n])
    fig.canvas.draw()
    fig.canvas.flush_events()

q_vals_square_vanleer = q_vals_square

# $\underline{\text{Problem 2 - Isothermal Shock Tube}}$

In [3]:
def tophat(x_val):
    if x_val > 0:
        return 1
    else:
        return 0
    
def flip_flop(vel_int):
    return 1 if vel_int >= 0 else -1

In [10]:
x_int = np.linspace(0,100,101,endpoint=True)

x_vals_2 = np.zeros(len(x_int)-1)

for i in range(len(x_vals_2)):
    x_vals_2[i] = (x_int[i]+x_int[i+1])/2
    
dx_2 = x_vals_2[1] - x_vals_2[0]

q_vals = np.zeros([3,len(x_vals_2)]) #Array for Primitive Variables
w_vals = np.zeros([2,len(x_vals_2)]) #Array for State (Conservative) Variables

sound_speed = np.ones(len(x_vals_2))
            
time = 0.0
eta_cfl = 0.5

#INITIAL CONDITION

for i in range(len(x_vals_2)):
    q_vals[0][i] = 2*tophat(50 - x_vals_2[i]) + 1
    q_vals[1][i] = 0 
    q_vals[2][i] = q_vals[0][i]*(sound_speed[i]**2)
             
    w_vals[0][i] = q_vals[0][i]
    w_vals[1][i] = q_vals[0][i]*q_vals[1][i]


fig, ax = plt.subplots(figsize=(14,8),dpi=80)
ax.plot(x_vals_2,q_vals[0],lw=3.0,ls='-.',color='k',label="Density - $\\rho$ at Time $t = 0.0$")
res0, = ax.plot(x_vals_2,q_vals[0],lw=3.0,ls='-',color='blue',label="Evolution of Density - $\\rho$")
res1, = ax.plot(x_vals_2,q_vals[1],lw=3.0,ls='-',color='red',label="Evolution of Velocity - $v$")
plt.xlabel("Increasing $x$ $\longrightarrow$",size=18)
plt.ylabel("Primitive Variables $\\rho$",size=18)
plt.title("Shock Tube Problem - Evolution",size=20,fontweight='bold')
plt.minorticks_on()
plt.xticks(size=18)
plt.yticks(size=18)
plt.legend(fontsize=15,facecolor='pink',loc="upper right")
plt.pause(2)

while time<=30.0:
    
    updated_w_array = w_vals
    updated_q_array = q_vals
    temp_w_array = w_vals
    
    v_vals_interface = np.zeros(len(x_int))
    flux_vals_interface = np.zeros([2,len(x_int)])
    
    a_array = np.zeros(len(x_vals_2))
    
    for i in range(len(x_vals_2)-1):
        a = max(abs(updated_q_array[1,i] - sound_speed[i]),
                abs(updated_q_array[1,i] + sound_speed[i]))
        
        a_array[i] = a
    
    dt_2 = eta_cfl * dx_2/max(a_array)
    
    for i in range(1,len(x_int)-1):
        v_vals_interface[i] = 0.5*((updated_w_array[1,i-1]/updated_w_array[0,i-1])
                                   + (updated_w_array[1,i]/updated_w_array[0,i]))
        
        theta = flip_flop(v_vals_interface[i])
        
        flux_vals_interface[0,i] = 0.5*v_vals_interface[i]*((1+theta)*updated_w_array[0,i-1] 
                                                          + (1-theta)*updated_w_array[0,i])
        flux_vals_interface[1,i] = 0.5*v_vals_interface[i]*((1+theta)*updated_w_array[1,i-1] 
                                                          + (1-theta)*updated_w_array[1,i])
    
    for i in range(1,len(x_vals_2)-1):
        temp_w_array[0,i] = updated_w_array[0,i] - ((dt_2/dx_2)*(flux_vals_interface[0,i+1]
                                                                 - flux_vals_interface[0,i]))
        temp_w_array[1,i] = updated_w_array[1,i] - ((dt_2/dx_2)*(flux_vals_interface[1,i+1]
                                                                 - flux_vals_interface[1,i]))
        
        updated_w_array[0,i] = temp_w_array[0,i]
    
    for i in range(1,len(x_vals_2)-1):
        updated_w_array[1,i] = temp_w_array[1,i] - 0.5*((sound_speed[i]**2)*(temp_w_array[0,i+1] 
                                                                             - temp_w_array[0,i-1])/dx_2)
    updated_w_array[0,0] = updated_w_array[0,1]
    updated_w_array[0,-1] = updated_w_array[0,-2]
    
    updated_w_array[1,0] = -updated_w_array[1,1]
    updated_w_array[1,-1] = -updated_w_array[1,-2]
    
    w_vals = updated_w_array

    q_vals[0] = w_vals[0]      
    q_vals[1] = w_vals[1]/w_vals[0]
    q_vals[2] = w_vals[0]*(sound_speed**2)
    
    time += dt_2
    
    res0.set_ydata(q_vals[0])
    res1.set_ydata(q_vals[1])
    fig.canvas.draw()
    fig.canvas.flush_events()